In [6]:
import sys
import numpy as np
import jieba
jieba.set_dictionary('dict.txt.big')
import gensim
import csv
import _pickle as cPickle
from sklearn.externals import joblib
from string import digits
import bz2
import pyLDAvis
import pyLDAvis.gensim

In [2]:
from elasticsearch import Elasticsearch
import elasticsearch.helpers
from datetime import datetime

es = Elasticsearch([{'host': 'localhost', 'port': 9200}])

In [5]:
def replace_content(content):
    res = content.replace('\n',' ') # replace \n
    return res

In [6]:
docs = list(elasticsearch.helpers.scan(es, index="pixnet", doc_type='food'))
total_content = [replace_content(doc['_source'].get('content')) for doc in docs]
print(len(total_content))

9597


In [7]:
def jieba_tokenize(content):
    return list(filter(None, jieba.cut(content, cut_all=True)))
total_word_list = [jieba_tokenize(content) for content in total_content]

Building prefix dict from /home/yenhao/Documents/pixnet/content_similarity/dict.txt.big ...
Loading model from cache /tmp/jieba.udc5b53799b274553d7fa5513aaa11a93.cache
Loading model cost 2.110 seconds.
Prefix dict has been built succesfully.


In [9]:
dictionary = gensim.corpora.Dictionary(total_word_list)
print(dictionary[5])
print(dictionary.token2id['週末'])
print("Number of words in dictionary:",len(dictionary))

更
238
Number of words in dictionary: 127306


In [10]:
corpus = [dictionary.doc2bow(article) for article in total_word_list]

In [11]:
lda = gensim.models.ldamulticore.LdaMulticore(corpus, id2word=dictionary, 
                                              num_topics=200, chunksize=1000, passes=20, workers=5)

In [12]:
dictionary.save_as_text('food_jieba_cutAll_dictionary.txt')

In [13]:
joblib.dump(lda, 'ldamodel_food.pkl')

['ldamodel_food.pkl']

In [22]:
corpora.MmCorpus.serialize('corpus_food.mm', corpus)

In [14]:
print(corpus[0])

[(0, 1), (1, 1), (2, 3), (3, 2), (4, 10), (5, 2), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 3), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 3), (21, 1), (22, 3), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 1), (30, 2), (31, 2), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 1), (39, 1), (40, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 2), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1), (58, 1), (59, 1), (60, 12), (61, 1), (62, 1), (63, 1), (64, 4), (65, 1), (66, 1), (67, 1), (68, 3), (69, 2), (70, 1), (71, 22), (72, 1), (73, 1), (74, 3), (75, 3), (76, 2), (77, 1), (78, 2), (79, 1), (80, 1), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 1), (94, 1), (95, 1), (96, 3), (97, 1), (98, 1), (99, 1), (100, 1), (101, 1), (102, 1), (103, 10), (104, 1), (105, 1), (106, 2), (107, 1), (108, 1), (109, 1), (110,

In [3]:
dictionary = gensim.corpora.Dictionary.load_from_text('food_jieba_cutAll_dictionary.txt')
corpus = gensim.corpora.MmCorpus('corpus_food.mm')
lda = joblib.load('ldamodel_food.pkl')

(lda.print_topics(num_topics=20, num_words=8))

[(7,
  '0.026*"台" + 0.021*"南投" + 0.016*"東" + 0.014*"cc" + 0.014*"wretch" + 0.011*"的" + 0.010*"景點" + 0.008*"境"'),
 (186,
  '0.046*"蔥油" + 0.044*"油餅" + 0.044*"蔥油餅" + 0.039*"的" + 0.019*"太郎" + 0.010*"驛站" + 0.008*"阿薩姆" + 0.007*"是"'),
 (161,
  '0.164*"雙" + 0.065*"i" + 0.053*"連站" + 0.022*"古屋" + 0.022*"名古屋" + 0.022*"名古" + 0.013*"miss" + 0.009*"v"'),
 (193,
  '0.110*"false" + 0.063*"w" + 0.040*"Name" + 0.040*"LsdException" + 0.040*"Locked" + 0.039*"Priority" + 0.034*"UnhideWhenUsed" + 0.033*"SemiHidden"'),
 (170,
  '0.031*"香港" + 0.018*"www" + 0.016*"http" + 0.015*"com" + 0.014*"00" + 0.012*"幣" + 0.011*"折" + 0.009*"優惠"'),
 (123,
  '0.039*"的" + 0.030*"咖啡" + 0.017*"下午茶" + 0.017*"下午" + 0.010*"店" + 0.010*"有" + 0.009*"咖啡館" + 0.009*"甜點"'),
 (30,
  '0.042*"的" + 0.018*"午餐" + 0.017*"早" + 0.015*"咖啡" + 0.014*"我" + 0.013*"是" + 0.012*"美式" + 0.011*"店"'),
 (69,
  '0.049*"東京" + 0.021*"飯店" + 0.020*"日本" + 0.015*"分鐘" + 0.014*"推薦" + 0.013*"新宿" + 0.012*"機場" + 0.009*"必"'),
 (90,
  '0.036*"tabelog" + 0.035*"000" + 0.03

In [4]:
lda_vis = pyLDAvis.gensim.prepare(lda, corpus, dictionary)


/usr/local/lib/python3.5/dist-packages/pyLDAvis/_prepare.py:387: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate_ix
  topic_term_dists = topic_term_dists.ix[topic_order]


In [5]:
pyLDAvis.display(lda_vis)